In [0]:
displayHTML("""<h1 style="background-color: #000020; color: white; text-align:center"><b>ETFs in Asset Owner Portfolios - 2024</b></h1>
            <h2 style="background-color: #000020; color: white; text-align:center"><b>by Tom Mason, Senior Research Analyst - S&P Global Market Intelligence FIG Research - March 2024 </b></h2>
            """)

ETFs in Asset Owner Portfolios - 2024 
 by Tom Mason, Senior Research Analyst - S&P Global Market Intelligence FIG Research - March 2024

## Contents

**Introduction:** This notebook pulls a decade of quarterly data on ETFs held by U.S. and Canadian pension plans and sovereign wealth funds, including the tickers, number of shares held and the market value of each plan's holdings.

**Data Sets:** The datasets used include Ownership, Market Data, and S&P Capital IQ Base Files.

**Libraries:** Import the Python and PySpark libraries needed for the data collection and analysis.

**Collecting Data:** Custom functions to pull data from the data catalog.

Analysis and Results: Sample chart showing growth in market value of ETF holdings over the past 10 years.

Direct your questions to Tom Mason, Senior Research Analyst, S&P Global Market Intelligence FIG Research | thomas.mason@spglobal.com.

## 1. Introduction 

This notebook provides an introduction to the following:

-  Finding quarterly amounts of ETF shares held by U.S. and Canadian pensions plans and sovereign wealth funds.  
- Calculating market values of holdings using closing prices and exchange rates.  
- Finding information on pension plans and sovereign wealth funds using the company intelligence database.  

This notebook accompanies the publication <a href='https://www.spglobal.com/spdji/en/research/article/etfs-in-asset-owner-portfolios/'>'ETFs in Asset Owner Portfolios - 2024'</a> by Ramachandran & Mason (March 2024). It provides the code necessary to replicate the security ownership data and pension plan metadata contained in the report.  

The Securities Exchange Commission (SEC) requires institutional investment managers to file quarterly statements detailing the publicly traded equities they hold. S&P Global Market Intelligence (SPGMI) makes this data available in aggregate form via data feeds, which we used to perform this analysis. We extracted the quarterly ETF holdings, both current and historical, of U.S. and Canadian pension plans and sovereign wealth funds from the first quarter of 2013 through the fourth quarter of 2023. Please see the aforementioned paper for further discussion of the methodology.

## 2. Data Sets

|Name|Type|Description|
|---|---|---|
|<a target="_blank" rel="noopener noreferrer" href="https://www.marketplace.spglobal.com/en/datasets/ownership-(20)">Ownership</b></a> | <a target="_blank" rel="noopener noreferrer" href="https://www.marketplace.spglobal.com/en/datasets"> Datasets </b></a>| The Ownership dataset provides detailed institutional, mutual fund and insiders/individuals equity share ownership data for public companies along with public float shares, buys and sells of insiders and major shareholders. |
| <a target="_blank" rel="noopener noreferrer" href="https://www.marketplace.spglobal.com/en/datasets/market-data-(17)">Market Data</b></a> |<a target="_blank" rel="noopener noreferrer" href="https://www.marketplace.spglobal.com/en/datasets"> Datasets | Access End of Day (EOD) traded currency, both split-adjusted and as quoted pricing data across open, close, high, low, volume, adjustment factor, shares outstanding, volume-weighted average price and other data points. |
| <a target="_blank" rel="noopener noreferrer" href="https://www.support.marketplace.spglobal.com/en/datasets/ciq/basefiles/base-files-user-guide#sec0">S&P Capital IQ Base Files</b></a> |<a target="_blank" rel="noopener noreferrer" href="https://www.marketplace.spglobal.com/en/datasets"> Datasets | The Base Files are the required foundation for all other S&P Capital IQ data. The base files enable you to use all other S&P Capital IQ data by associating companies, symbols, securities and other base objects across all S&P Capital IQ data sets. |



### Instructions  
1. Import libraries.  
2. Click Run all button to run all cells.  
3. Change filing date and trade date in get_etf_holdings function to analyze different periods.  

## 3. Libraries  
Import Python and PySpark libraries.

In [0]:
from datetime import datetime,timedelta
from pyspark.sql.functions import *

## 4. Collecting Data
The get_trade_date function returns either the date of the period's end or, if it's a weekend and the markets are closed, the weekday immediately prior to it.  

The get_etf_holdings function returns all the ETFs held by U.S. and Canadian pension plans and sovereign wealth funds that file 13Fs for a given filing date, along with a calculation of the market value of those holdings based on the trade date.

#### 4.1 Get Trade Dates and ETF Holdings  
Use these two functions to gather data.

In [0]:
def get_trade_date(filing_date):
    # create a function that pulls the most recent weekday, based on filing date
    # in weekday() function, 0 = Mon, 5 = Sat, 6 = Sun
    trade_date = datetime.strptime(filing_date,'%Y-%m-%d')
    dow = trade_date.weekday()
    if dow == 5:
        trade_date = trade_date - timedelta(days=1)
    if dow == 6:
        trade_date = trade_date - timedelta(days=2)
    return datetime.strftime(trade_date,'%Y-%m-%d')

def get_etf_holdings(filing_date,trade_date):
  
  # select database
  spark.sql(f"""use ownership;""")

  etf_holdings = spark.sql(f"""
    select hp.PERIODENDDATE,h.OWNEROBJECTID,ti.TICKERSYMBOL as ETFTICKER,h.SHARESHELD,((pe.PRICECLOSE * h.SHARESHELD)/er.PRICECLOSE) as MARKETVALUE
    from ownership.ciqownissueholding h
    full outer join ownership.ciqownholdingperiod hp on hp.PERIODID = h.PERIODID
    full outer join basedata.ciqSecurity s on s.securityId = h.securityId
    full outer join basedata.ciqTradingItem ti on s.securityId = ti.securityId
    full outer join marketdata.ciqPriceEquity pe on pe.tradingItemId = ti.tradingItemId
    full outer join basedata.ciqcompany c on c.companyId = s.companyId
    full outer join basedata.ciqSecurityToSecurityFeature ssf on s.securityid = ssf.securityId
    full outer join basedata.ciqExchange e on e.EXCHANGEID = ti.EXCHANGEID
    full outer join basedata.ciqcompany hc on hc.companyId = h.OWNEROBJECTID
    full outer join ownership.ciqowncompanytoinsttype c2i on hc.COMPANYID = c2i.COMPANYID
    full outer join ownership.ciqowninstitutiontype it on c2i.INSTITUTIONTYPEID = it.INSTITUTIONTYPEID
    full outer join basedata.ciqexchangerate er on er.CURRENCYID = e.CURRENCYID
    full outer join ownership.ciqOwnIssueHoldingDocument hd on hd.ownerObjectId = h.ownerObjectId and hd.periodId = h.periodid and hd.securityId = h.securityId -- limit to 13F filings
    full outer join basedata.ciqdocumenttoformtype dtft on dtft.DOCUMENTID = hd.DOCUMENTID -- limit to 13F filings
    where ssf.securityFeatureId = 3 -- ETF
    and pe.PRICINGDATE = '{trade_date}'
    and er.PRICEDATE = '{trade_date}'
    and hp.PERIODENDDATE = '{filing_date}'
    and ti.PRIMARYFLAG = 1 -- primary listing
    and h.SHARESHELD <> 0 -- exclude closed out positions
    and er.LATESTSNAPFLAG = 1 -- final exchange rate
    and dtft.DOCUMENTFORMTYPEID IN (35,36) -- 13F-HR, 13F-HR/A
    and h.OWNEROBJECTID IN (
      select c.COMPANYID
      from ciqowncompanytoinsttype c2i
      join ciqowninstitutiontype it on c2i.INSTITUTIONTYPEID = it.INSTITUTIONTYPEID
      join basedata.ciqcompany c on c2i.COMPANYID = c.COMPANYID
      where it.INSTITUTIONTYPEID in (5,6,10,13,14,15) -- pension plans and SWFs
      and c.COUNTRYID in (37,213) --US and Canadian investors
    )
    and h.LATESTFLAG = 0 -- limit to historical data
    order by hc.COMPANYNAME asc
    """)
  return etf_holdings

This code retrieves ETF holdings data for each quarter and combines it into one dataframe.

In [0]:
# quarterly dates
q_dates = []
start_year = 2013

for i in range(11):
  q_dates.append(str(start_year + i) + "-03-31")
  q_dates.append(str(start_year + i) + "-06-30")
  q_dates.append(str(start_year + i) + "-09-30")
  q_dates.append(str(start_year + i) + "-12-31")

q_dates

# create initial dataframe using first year
trade_date_1 = get_trade_date(q_dates[0])
etf_df = get_etf_holdings(q_dates[0],trade_date_1)

for k in range(1,len(q_dates)):
  filing_date = q_dates[k]
  trade_date = get_trade_date(q_dates[k])
  new_etf_holdings = get_etf_holdings(filing_date,trade_date)
  etf_df = etf_df.union(new_etf_holdings)

#### 4.2 Add Holdings From Trade Dates On Holidays    
In instances where the markets were closed on the given weekday, we ran the functions using the trade date prior.

In [0]:
q1_13 = get_etf_holdings('2013-03-31','2013-03-28')
q1_18 = get_etf_holdings('2018-03-31','2018-03-29')
etf_df = etf_df.union(q1_13)
etf_df = etf_df.union(q1_18)

#### 4.3 Cast Columns to Different Types

In [0]:
etf_df = etf_df.withColumn("OWNEROBJECTID",etf_df.OWNEROBJECTID.cast("int")) \
  .withColumn("SHARESHELD",etf_df.SHARESHELD.cast("int")) \
  .withColumn("MARKETVALUE",etf_df.MARKETVALUE.cast("float"))

#### 4.4 Get Asset Owner Metadata
Pull in information on the U.S. and Canadian pension plans and sovereign wealth funds that file 13Fs.

In [0]:
%sql use ownership;
select distinct h.OWNEROBJECTID,c.COMPANYNAME,c.STREETADDRESS,s.STATE,g.COUNTRY,it.INSTITUTIONTYPENAME
from ciqownissueholding h
full outer join ciqOwnIssueHoldingDocument hd on hd.ownerObjectId = h.ownerObjectId and hd.periodId = h.periodid -- limit to 13F filings
full outer join basedata.ciqdocumenttoformtype dtft on dtft.DOCUMENTID = hd.DOCUMENTID -- limit to 13F filings
full outer join basedata.ciqcompany c on h.OWNEROBJECTID = c.COMPANYID
full outer join basedata.ciqstate s on s.STATEID = c.STATEID and s.COUNTRYID = c.COUNTRYID
full outer join basedata.ciqcountrygeo g on g.COUNTRYID = c.COUNTRYID
full outer join ciqowncompanytoinsttype c2i on c2i.COMPANYID = h.OWNEROBJECTID
full outer join ciqowninstitutiontype it on c2i.INSTITUTIONTYPEID = it.INSTITUTIONTYPEID
where dtft.DOCUMENTFORMTYPEID IN (35,36) -- 13F-HR, 13F-HR/A
and h.OWNEROBJECTID IN (
  select c.COMPANYID
  from ciqowncompanytoinsttype c2i
  join ciqowninstitutiontype it on c2i.INSTITUTIONTYPEID = it.INSTITUTIONTYPEID
  join basedata.ciqcompany c on c2i.COMPANYID = c.COMPANYID
  where it.INSTITUTIONTYPEID in (5,6,10,13,14,15) -- pension plans and SWFs
  and c.COUNTRYID in (37,213) --US and Canadian investors
)
order by c.COMPANYNAME asc

OWNEROBJECTID COMPANYNAME STREETADDRESS STATE COUNTRY INSTITUTIONTYPENAME 216396439 Akaloa Resource Foundation, Endowment Arm 6889 Rowland Road Minnesota United States Foundation Fund Sponsor 7714694 Alaska Permanent Fund 801 West 10th Street Alaska United States Sovereign Wealth Fund 28689642 Alaska Retirement Management Board 333 Willoughby Avenue Alaska United States Government Pension Plan Sponsor 28363594 Alberta Investment Management Corporation 10250 101 Street North West Alberta Canada Government Pension Plan Sponsor 24404076 Amelia Peabody Foundation, Endowment Arm One Hollis Street Massachusetts United States Foundation Fund Sponsor 6058869 American Bible Society, Endowment Arm 1865 Broadway New York United States Endowment Fund Sponsor 6037332 Arizona State Retirement System 3300 North Central Avenue Arizona United States Government Pension Plan Sponsor 653319011 B.O.S.S. Retirement Advisors, LLC 3400 Ashton Boulevard Utah United States Corporate Pension Plan Sponsor 27060997 Bill & Melinda Gates Foundation Trust 2365 Carillon Point Washington United States Foundation Fund Sponsor 3375244 British Columbia Investment Management Corporation 750 Pandora Ave British Columbia Canada Government Pension Plan Sponsor 3533816 Brown University Endowment Investment Office Rhode Island United States Endowment Fund Sponsor 161245 California Public Employees' Retirement System Lincoln Plaza East California United States Government Pension Plan Sponsor 922073 California State Teachers' Retirement System 100 Waterfront Place California United States Government Pension Plan Sponsor 1871799138 Call To Action Foundation, Endowment Arm 185 South State Street, Suite 1300 Utah United States Foundation Fund Sponsor 2334713 Canada Pension Plan Investment Board One Queen Street East Ontario Canada Government Pension Plan Sponsor 3533796 Carnegie Mellon University Endowment Arm Office of the Campaign Pennsylvania United States Endowment Fund Sponsor 1860944217 Chan Zuckerberg Initiative, Llc, Endowment arm 2682 Middlefield Rd, Suite I California United States Foundation Fund Sponsor 24885638 Charles Stewart Mott Foundation, Endowment Arm 503 South Saginaw Street Michigan United States Foundation Fund Sponsor 24049012 Chas. P. Smith & Associates, PA, CPAS 205 East Orange Street Florida United States Corporate Pension Plan Sponsor 59042438 Columbia Investment Management Company 405 Lexington Avenue New York United States Endowment Fund Sponsor 6089954 Conrad N. Hilton Foundation Inc., Endowment Fund 100 West Liberty Street Nevada United States Foundation Fund Sponsor 3533842 Cornell University, Endowment Arm 1155 Avenue of the Americas New York United States Endowment Fund Sponsor 654698504 Dan L Duncan Foundation, Endowment Arm null null United States Foundation Fund Sponsor 3533836 Dartmouth College, Endowment Arm One Rope Ferry Road New Hampshire United States Endowment Fund Sponsor 60075539 Deseret Mutual Benefit Administrators, Asset Management Arm 60 East South Temple Utah United States Corporate Pension Plan Sponsor 285127763 Diana Davis Spencer Foundation, Endowment Arm 3 Bethesda Metro Center Maryland United States Foundation Fund Sponsor 6074152 Duke Endowment, Endowment Arm 100 North Tryon Street North Carolina United States Foundation Fund Sponsor 3536042 Duke Management Company 280 S Mangum Street North Carolina United States Endowment Fund Sponsor 654923665 Ebor Charitable Trust, Endowment Arm 255 Buffalo Way Wyoming United States Foundation Fund Sponsor 3647325 Elca Board of Pensions 800 Marquette Avenue Minnesota United States Endowment Fund Sponsor 3533554 Emory Investment Management Two Live Oak Center Georgia United States Endowment Fund Sponsor 6167587 Employees Retirement System of Texas 200 East 18th Street Texas United States Government Pension Plan Sponsor 12632780 Ensign Peak Advisors, Inc. 50 East North Temple Utah United States Endowment Fund Sponsor 24868860 Exxon Investment Management, Inc. null null United States 

#### 4.5 Download Holdings Data Locally  
To download PySpark data, run the display function, then click the download button (the one to the right downloads the entire dataset if more than 10,000 rows).

In [0]:
display(etf_df)

PERIODENDDATE OWNEROBJECTID ETFTICKER SHARESHELD MARKETVALUE 2013-06-30T00:00:00.000+0000 6167587 IGIB 11800000 6.3553619E8 2013-06-30T00:00:00.000+0000 6167587 IVW 200000 4200500.0 2013-06-30T00:00:00.000+0000 6167587 PPLT 11000 1441880.0 2013-06-30T00:00:00.000+0000 6167587 IJH 240000 5544000.0 2013-06-30T00:00:00.000+0000 6167587 PALL 37000 2392050.0 2013-06-30T00:00:00.000+0000 6167587 DXJ 525000 2.394525E7 2013-06-30T00:00:00.000+0000 6167587 EMB 2000472 2.19111696E8 2013-06-30T00:00:00.000+0000 6167587 DGS 220000 1.01288E7 2013-06-30T00:00:00.000+0000 6167587 LQD 5508535 6.2604499E8 2013-06-30T00:00:00.000+0000 6167587 HYG 2892450 2.62865856E8 2013-06-30T00:00:00.000+0000 6167587 IYR 22000 1461460.0 2013-06-30T00:00:00.000+0000 6167587 EWM 75000 4665000.0 2013-09-30T00:00:00.000+0000 6167587 LQD 3720030 4.22297792E8 2013-09-30T00:00:00.000+0000 6167587 HYG 2892450 2.64890576E8 2013-09-30T00:00:00.000+0000 6167587 EEM 50000 2037750.0 2013-09-30T00:00:00.000+0000 6167587 IJH 945000 2.346246E7 2013-09-30T00:00:00.000+0000 6167587 FXI 200000 7416000.0 2013-09-30T00:00:00.000+0000 6167587 DXJ 550000 2.63615E7 2013-09-30T00:00:00.000+0000 6167587 IGIB 8731600 4.712008E8 2013-09-30T00:00:00.000+0000 6167587 EMB 1667472 1.81801136E8 2013-09-30T00:00:00.000+0000 6167587 PPLT 11000 1510520.0 2013-09-30T00:00:00.000+0000 6167587 IVW 131600 2939944.0 2013-09-30T00:00:00.000+0000 6167587 PALL 37000 2617380.0 2013-12-31T00:00:00.000+0000 6167587 EMB 1274300 1.37828288E8 2013-12-31T00:00:00.000+0000 6167587 HYG 3682140 3.41997152E8 2013-12-31T00:00:00.000+0000 6167587 FXI 200000 7674000.0 2013-12-31T00:00:00.000+0000 6167587 DXJ 550000 2.7962E7 2013-12-31T00:00:00.000+0000 6167587 PALL 37000 2575940.0 2013-12-31T00:00:00.000+0000 6167587 PPLT 11000 1472790.0 2013-12-31T00:00:00.000+0000 24868860 IVV 38156 7083661.5 2013-12-31T00:00:00.000+0000 20889 IVV 127807 2.372737E7 2013-12-31T00:00:00.000+0000 20889 PAGG 444299 1.3289427E7 2013-12-31T00:00:00.000+0000 20889 HYG 591029 5.4894772E7 2014-03-31T00:00:00.000+0000 20889 PAGG 359862 1.0954199E7 2014-03-31T00:00:00.000+0000 20889 HYG 795029 7.5042784E7 2014-03-31T00:00:00.000+0000 3533848 GDX 10209 240983.44 2014-03-31T00:00:00.000+0000 3533848 SPY 2137117 3.9966224E8 2014-03-31T00:00:00.000+0000 3533848 EEM 5000 205050.0 2014-03-31T00:00:00.000+0000 3533848 IWM 350000 4.0719E7 2014-06-30T00:00:00.000+0000 20889 IVV 122905 2.4212284E7 2014-06-30T00:00:00.000+0000 20889 FXI 611782 2.2660406E7 2014-06-30T00:00:00.000+0000 20889 SPSM 335757 7939533.5 2014-06-30T00:00:00.000+0000 20889 GLD 15891 2034683.6 2014-06-30T00:00:00.000+0000 20889 DBE 163429 5025442.0 2014-09-30T00:00:00.000+0000 20889 DBE 161930 4359139.5 2014-09-30T00:00:00.000+0000 20889 IJH 318140 8700493.0 2014-09-30T00:00:00.000+0000 20889 EWM 74485 4588276.0 2014-09-30T00:00:00.000+0000 3533848 EEM 5000 207800.0 2014-09-30T00:00:00.000+0000 3533848 EFA 5000 320600.0 2014-09-30T00:00:00.000+0000 3533848 SPY 850000 1.67467008E8 2014-09-30T00:00:00.000+0000 3533848 GDX 21360 456185.53 2014-09-30T00:00:00.000+0000 3533848 IWM 100000 1.0935E7 2014-09-30T00:00:00.000+0000 3533848 EWJ 63750 3001350.0 2014-12-31T00:00:00.000+0000 54631718 XLF 150000 3709500.0 2014-12-31T00:00:00.000+0000 20889 HYG 108900 9757440.0 2014-12-31T00:00:00.000+0000 20889 EWM 74485 4016231.2 2014-12-31T00:00:00.000+0000 20889 VWO 134487 5382169.5 2014-12-31T00:00:00.000+0000 20889 EWY 811262 4.4854676E7 2014-12-31T00:00:00.000+0000 20889 INDA 30000 898500.0 2014-12-31T00:00:00.000+0000 20889 VEA 312759 1.1847311E7 2014-12-31T00:00:00.000+0000 20889 DBE 148551 2595186.0 2014-12-31T00:00:00.000+0000 20889 IDX 882463 2.1435026E7 2015-03-31T00:00:00.000+0000 6167587 PALL 37000 2638470.0 2015-03-31T00:00:00.000+0000 24868860 IVV 111265 2.3124204E7 2015-03-31T00:00:00.000+0000 54631718 XLF 150000 3616500.0 2015-03-31T00:00:00.000+0000 20889 IDX 931665 2.2965542E7 2015-03-31T00:00:00.000+0000 20889 SPSM 236955 5854368.0 2015-03-31T00:00:00.000+0000 20889 VIG 75315

In [0]:
# optional: convert to Pandas dataframe
# etf_df_pd = etf_df.toPandas()

## 5. Analysis and Results

#### 5.1 Growth in market value of ETF holdings
As of year-end 2023, asset owners had $56 billion invested in ETFs. ETF usage began increasing in December 2016 and between Q3 and Q4 of 2019 ETF AUM doubled. This analysis is limited to U.S. and Canadian pension plans and sovereign wealth funds.  

In [0]:
# filter data to year-end values
ye_df = etf_df.withColumn('MONTH',date_format("PERIODENDDATE","M"))
ye_df = ye_df.filter(ye_df.MONTH == 12)
# add column to show year
ye_df = ye_df.withColumn('YEAR',date_format("PERIODENDDATE","y"))
# convert to billions
ye_df = ye_df.withColumn('MARKETVALUE',ye_df.MARKETVALUE / 1000000000)
display(ye_df)

PERIODENDDATE OWNEROBJECTID ETFTICKER SHARESHELD MARKETVALUE MONTH YEAR 2013-12-31T00:00:00.000+0000 28363594 IWO 167830 0.022742644 12 2013 2013-12-31T00:00:00.000+0000 6037332 QUAL 2150000 0.121518 12 2013 2013-12-31T00:00:00.000+0000 3375244 DSI 30000 0.0010365 12 2013 2013-12-31T00:00:00.000+0000 3375244 SPY 124085 0.022917258 12 2013 2013-12-31T00:00:00.000+0000 3375244 EFA 31000 0.002079945 12 2013 2013-12-31T00:00:00.000+0000 161245 EPI 417000 0.00727248 12 2013 2013-12-31T00:00:00.000+0000 161245 EWX 6909867 0.320686912 12 2013 2013-12-31T00:00:00.000+0000 161245 XLB 54604 0.002523797 12 2013 2013-12-31T00:00:00.000+0000 161245 IWO 400 5.4204E-5 12 2013 2013-12-31T00:00:00.000+0000 161245 AAXJ 127904 0.00771389 12 2013 2013-12-31T00:00:00.000+0000 161245 IWM 3110 3.5876959375E-4 12 2013 2013-12-31T00:00:00.000+0000 161245 EWJ 221261 0.010743549 12 2013 2013-12-31T00:00:00.000+0000 161245 SPY 221035 0.040822956 12 2013 2013-12-31T00:00:00.000+0000 161245 VGK 457081 0.026876362 12 2013 2013-12-31T00:00:00.000+0000 2334713 EWZ 1200000 0.053616 12 2013 2013-12-31T00:00:00.000+0000 2334713 EFA 2100000 0.140899504 12 2013 2013-12-31T00:00:00.000+0000 2334713 QQQ 25300 0.002225388 12 2013 2013-12-31T00:00:00.000+0000 24885638 IJH 962500 0.025758424 12 2013 2013-12-31T00:00:00.000+0000 24049012 EEM 54855 0.00229266475 12 2013 2013-12-31T00:00:00.000+0000 24049012 SPXL 265764 0.004238936 12 2013 2013-12-31T00:00:00.000+0000 24049012 FAS 90744 0.00204854575 12 2013 2013-12-31T00:00:00.000+0000 24049012 AMLP 6789 6.038815625E-4 12 2013 2013-12-31T00:00:00.000+0000 24049012 VWO 246819 0.010154134 12 2013 2013-12-31T00:00:00.000+0000 24049012 CURE 116880 0.00201939425 12 2013 2013-12-31T00:00:00.000+0000 24049012 DVY 26382 0.00188235575 12 2013 2013-12-31T00:00:00.000+0000 24049012 MIDU 102480 0.002047806625 12 2013 2013-12-31T00:00:00.000+0000 24049012 IJJ 398852 0.023179284 12 2013 2013-12-31T00:00:00.000+0000 24049012 IXC 503386 0.021756342 12 2013 2013-12-31T00:00:00.000+0000 24049012 EEMV 178284 0.010386826 12 2013 2013-12-31T00:00:00.000+0000 24049012 IJT 85506 0.0050709335 12 2013 2013-12-31T00:00:00.000+0000 24049012 QQQ 419865 0.036931324 12 2013 2013-12-31T00:00:00.000+0000 24049012 IVV 244784 0.045444148 12 2013 2013-12-31T00:00:00.000+0000 24049012 IJS 384308 0.021379054 12 2013 2013-12-31T00:00:00.000+0000 24049012 TNA 56118 0.00217260825 12 2013 2013-12-31T00:00:00.000+0000 24049012 EET 25500 0.001935195 12 2013 2013-12-31T00:00:00.000+0000 24049012 ERX 2392 0.0021499295 12 2013 2013-12-31T00:00:00.000+0000 24049012 HDV 31653 0.00222362325 12 2013 2013-12-31T00:00:00.000+0000 24049012 SSO 174000 0.00223068 12 2013 2013-12-31T00:00:00.000+0000 24049012 ISCG 1232946 0.027223036 12 2013 2013-12-31T00:00:00.000+0000 24049012 TECL 951000 0.0021706575 12 2013 2013-12-31T00:00:00.000+0000 24049012 IYG 1709031 0.047704752 12 2013 2013-12-31T00:00:00.000+0000 24049012 IWM 19094 0.00220268375 12 2013 2013-12-31T00:00:00.000+0000 24049012 IWR 19800 7.42401E-4 12 2013 2013-12-31T00:00:00.000+0000 24049012 IJK 896724 0.033669744 12 2013 2013-12-31T00:00:00.000+0000 24049012 IDV 745929 0.028300546 12 2013 2013-12-31T00:00:00.000+0000 3533836 AAXJ 449200 0.027091252 12 2013 2013-12-31T00:00:00.000+0000 3533836 GLD 589932 0.068502904 12 2013 2013-12-31T00:00:00.000+0000 3533836 EEM 362645 0.015156748 12 2013 2013-12-31T00:00:00.000+0000 3533836 SPY 104206 0.019245806 12 2013 2013-12-31T00:00:00.000+0000 3533554 FRI 268 4.70072021484375E-6 12 2013 2013-12-31T00:00:00.000+0000 3533554 DDM 420 8.0577001953125E-6 12 2013 2013-12-31T00:00:00.000+0000 3533554 USRT 80 3.040800048828125E-6 12 2013 2013-12-31T00:00:00.000+0000 3533554 VIG 2546 1.91561046875E-4 12 2013 2013-12-31T00:00:00.000+0000 3533554 REZ 50 2.2555E-6 12 2013 2013-12-31T00:00:00.000+0000 3533554 EWH 248 5.1087998046875E-6 12 2013 2013-12-31T00:00:00.000+0000 3533554 IWC 60 4.5072001953125E-6 12 2013 2013-12-31T00:00:00.000+0000 3533554 VTV 109 8.326509765625E-6 12 2013 201

Databricks visualization. Run in Databricks to view.